# Optimize Initial Conditions
## Yabox

In [1]:
from scipy.optimize import brute
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
from yabox import DE

# Load solver

In [2]:
LoadBH=True
if LoadBH:
    import LearnerICRayNoLoadBH as L 
else:
    import LearnerICRayNoLoad as L 

# Load Data

In [3]:
def load_confirmed(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y
    return df2

def load_dead(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    return df2

# Data for States

In [4]:
dfparam = pd.read_csv("data/param.csv")
dfparam

state  start-date  prediction-range         s0  e0  a0   i0   r0   d0  \
0    SP  2020-03-15               200  8000000.0   0   0  800  300  250   
1    ES  2020-04-01               200   475000.0   0   0   50  250   50   
2    MG  2020-04-01               200  1100000.0   0   0  200  250   40   
3    RJ  2020-03-20               200   700000.0   0   0  800  250   50   
4    CE  2020-03-20               200   800000.0   0   0  800  250   50   
5    PE  2020-03-20               200   700000.0   0   0  800  250  100   
6    AM  2020-03-20               200   700000.0   0   0  800  250  100   

   START  RATIO  WCASES  WREC  
0    100   0.15    0.55  0.01  
1    100   0.15    0.65  0.01  
2    100   0.15    0.55  0.01  
3    100   0.15    0.50  0.01  
4    100   0.15    0.50  0.01  
5    100   0.15    0.50  0.01  
6    100   0.15    0.50  0.01

In [5]:
df = pd.read_csv("data/dados_total_estados.csv")
df

index        date state   city place_type  confirmed  deaths  \
0          0  2020-06-06    SE  TOTAL      state       8972     208   
1          1  2020-06-05    SE  TOTAL      state       8577     198   
2          2  2020-06-04    SE  TOTAL      state       8200     186   
3          3  2020-06-03    SE  TOTAL      state       7989     180   
4          4  2020-06-02    SE  TOTAL      state       7555     172   
...      ...         ...   ...    ...        ...        ...     ...   
2244  158210  2020-03-11    BA  TOTAL      state          3       0   
2245  158211  2020-03-10    BA  TOTAL      state          2       0   
2246  158212  2020-03-09    BA  TOTAL      state          2       0   
2247  158213  2020-03-07    BA  TOTAL      state          2       0   
2248  158214  2020-03-06    BA  TOTAL      state          1       0   

      order_for_place  is_last      popEst  city_ibge_code  \
0                  74     True   2298696.0            28.0   
1                  73    False   2298696.0            28.0   
2                  72    False   2298696.0            28.0   
3                  71    False   2298696.0            28.0   
4                  70    False   2298696.0            28.0   
...               ...      ...         ...             ...   
2244                5    False  14873064.0            29.0   
2245                4    False  14873064.0            29.0   
2246                3    False  14873064.0            29.0   
2247                2    False  14873064.0            29.0   
2248                1    False  14873064.0            29.0   

      confirmed_per_100k_inhabitants  death_rate  
0                          390.30824      0.0232  
1                          373.12459      0.0231  
2                          356.72399      0.0227  
3                          347.54487      0.0225  
4                          328.66460      0.0228  
...                              ...         ...  
2244                         0.02017      0.0000  
2245                         0.01345      0.0000  
2246                         0.01345      0.0000  
2247                         0.01345      0.0000  
2248                         0.00672      0.0000  

[2249 rows x 13 columns]

# Functions for Optimization

In [6]:
from scipy.integrate import odeint
import os
import sys
import io
import ray
import gc
import tensorflow as tf

def create_f(state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):
                
    def fobjective(point):
        
        dead=  load_dead(state,date)
        data = load_confirmed(state,date)*(1-ratio)-dead
        
        cleanRecovered=False
        s0, deltaDate, i0, weigthCases, weigthRecov = point
        end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=+int(deltaDate))
                    
        f=L.Learner.remote(state, end_date.strftime("%Y-%m-%d"), predict_range,\
                           s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                           cleanRecovered, version, data, dead, savedata=False)
        result = f.train.remote() 
        result = ray.get(result) 

        del end_date,cleanRecovered, data, dead         

        gc.collect()

        return result
    return fobjective

In [7]:
@ray.remote(memory=50 * 1024 * 1024, max_calls=1)
def opt(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):

    bounds=[(0.8*s0,1.2*s0),(-10,10),(0.8*i0,1.2*i0),\
              (0.3,0.7),(.001,.05)]
    maxiterations=300
    f=create_f(state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version)
    de = DE(f, bounds, maxiters=maxiterations)
    for step in de.geniterator():
        try:
            idx = step.best_idx
            norm_vector = step.population[idx]
            best_params = de.denormalize([norm_vector])
            del norm_vector, idx
        except:
            print("error in function evaluation")
    p=best_params[0]
    del f, bounds, data, dead
    
    return p

# Main Code

In [ ]:
states=['SP','ES','MG','RJ','PE','CE','AM']
# states=['MG','RJ','PE','CE','AM']
allStates=True
version="101"
ray.shutdown()
GB=1024*1024*1024
MB=1024*1024
ray.init(object_store_memory=500*MB,memory=2*GB,lru_evict=True,\
         driver_object_store_memory=50*MB,num_cpus=16)
gc.enable()

optimal=[]
if allStates:
    for state in states:
        #remove previous history file
        strFile='./results/history_'+state+version+'.csv'
        if os.path.isfile(strFile):
            os.remove(strFile)
        query = dfparam.query('state == "{}"'.format(state)).reset_index()
        parameters = np.array(query.iloc[:, 2:])[0]
        date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
        optimal.append(opt.remote(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version))        
else:
    state = "ES" 
    #remove previous history file
    strFile='./results/history_'+state+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    start_date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    optimal.append(opt.remote(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version))        



In [ ]:
optimal=ray.get(optimal)


(pid=16719) basinhopping step 0: f 8.91186e+07
(pid=16710) basinhopping step 0: f 1.04694e+08
(pid=16721) basinhopping step 0: f 2.12044e+08
(pid=16719) basinhopping step 1: f 8.91186e+07 trial_f 8.92551e+07 accepted 0  lowest_f 8.91186e+07
(pid=16707) basinhopping step 0: f 1.00799e+09
(pid=16713) basinhopping step 0: f -3.91276e+11
(pid=16707) basinhopping step 1: f 1.00662e+09 trial_f 1.00662e+09 accepted 1  lowest_f 1.00662e+09
(pid=16707) found new global minimum on step 1 with function value 1.00662e+09
(pid=16770) basinhopping step 0: f -1.62725e+11
(pid=16719) basinhopping step 2: f -3.29792e+11 trial_f -3.29792e+11 accepted 1  lowest_f -3.29792e+11
(pid=16719) found new global minimum on step 2 with function value -3.29792e+11
(pid=16707) warning: basinhopping: local minimization failure
(pid=16707) basinhopping step 2: f 1.00662e+09 trial_f 1.04027e+12 accepted 0  lowest_f 1.00662e+09
(pid=16770) basinhopping step 1: f -1.62725e+11 trial_f 4.6202e+09 accepted 0  lowest_f -1.6

(pid=16715) basinhopping step 0: f 1.07868e+08
(pid=16770) basinhopping step 6: f -1.62725e+11 trial_f -4.99929e+10 accepted 0  lowest_f -1.62725e+11
(pid=16713) basinhopping step 5: f -4.6025e+11 trial_f -3.9021e+11 accepted 0  lowest_f -4.6025e+11
(pid=16770) basinhopping step 7: f -1.62725e+11 trial_f 3.5341e+07 accepted 0  lowest_f -1.62725e+11
(pid=16770) basinhopping step 8: f -1.62725e+11 trial_f 4.73936e+10 accepted 0  lowest_f -1.62725e+11
(pid=16715) basinhopping step 1: f 1.07868e+08 trial_f 8.52552e+08 accepted 0  lowest_f 1.07868e+08
(pid=16721) warning: basinhopping: local minimization failure
(pid=16721) basinhopping step 6: f -1.53119e+11 trial_f 2.07206e+08 accepted 0  lowest_f -1.53119e+11
(pid=16713) warning: basinhopping: local minimization failure
(pid=16713) basinhopping step 6: f -4.6025e+11 trial_f 2.0629e+10 accepted 0  lowest_f -4.6025e+11
(pid=16715) basinhopping step 2: f 1.07868e+08 trial_f 8.53344e+08 accepted 0  lowest_f 1.07868e+08
(pid=16705) basinhoppi

(pid=16712) basinhopping step 4: f -3.80684e+11 trial_f 3.18979e+07 accepted 0  lowest_f -3.80684e+11
(pid=17419) warning: basinhopping: local minimization failure
(pid=17419) basinhopping step 6: f -7.26646e+11 trial_f -5.80412e+09 accepted 0  lowest_f -7.26646e+11
(pid=17466) warning: basinhopping: local minimization failure
(pid=17466) basinhopping step 2: f -2.07307e+11 trial_f 7.31383e+07 accepted 0  lowest_f -2.07307e+11
(pid=17418) basinhopping step 2: f -2.65468e+13 trial_f -2.65468e+13 accepted 1  lowest_f -2.65468e+13
(pid=17418) found new global minimum on step 2 with function value -2.65468e+13
(pid=17419) warning: basinhopping: local minimization failure
(pid=17419) basinhopping step 7: f -1.27734e+12 trial_f -1.27734e+12 accepted 1  lowest_f -1.27734e+12
(pid=17419) found new global minimum on step 7 with function value -1.27734e+12
(pid=17418) warning: basinhopping: local minimization failure
(pid=17418) basinhopping step 3: f -2.65468e+13 trial_f -3.10081e+11 accepted 0

(pid=17505) basinhopping step 9: f -4.13313e+11 trial_f 1.13513e+08 accepted 0  lowest_f -4.13313e+11
(pid=18639) basinhopping step 0: f 3.41502e+07
(pid=18638) basinhopping step 1: f 1.32837e+07 trial_f 1.34358e+07 accepted 0  lowest_f 1.32837e+07
(pid=17506) basinhopping step 7: f -2.63092e+11 trial_f 1.51209e+08 accepted 0  lowest_f -2.63092e+11
(pid=17505) basinhopping step 10: f -4.13313e+11 trial_f 1.26398e+09 accepted 0  lowest_f -4.13313e+11
(pid=17418) basinhopping step 9: f -6.82489e+13 trial_f -2.65483e+13 accepted 0  lowest_f -6.82489e+13
(pid=17506) basinhopping step 8: f -2.63092e+11 trial_f 1.03389e+08 accepted 0  lowest_f -2.63092e+11
(pid=18663) basinhopping step 0: f 8.3871e+07
(pid=18663) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=18663)   warnings.warn(warning_msg, ODEintWarning)
(pid=17418) bas

(pid=18662) basinhopping step 6: f -9.20021e+13 trial_f -3.02587e+13 accepted 0  lowest_f -9.20021e+13
(pid=18663) basinhopping step 9: f -6.92935e+11 trial_f 8.4169e+07 accepted 0  lowest_f -6.92935e+11
(pid=18638) basinhopping step 8: f -4.21184e+11 trial_f -3.63687e+11 accepted 0  lowest_f -4.21184e+11
(pid=18518) basinhopping step 10: f -1.26687e+12 trial_f 1.59548e+09 accepted 0  lowest_f -1.26687e+12
(pid=19121) basinhopping step 4: f -1.45791e+11 trial_f 1.24373e+08 accepted 0  lowest_f -1.45791e+11
(pid=18662) basinhopping step 7: f -9.20021e+13 trial_f 7.37569e+08 accepted 0  lowest_f -9.20021e+13
(pid=18663) basinhopping step 10: f -6.92935e+11 trial_f 8.5979e+07 accepted 0  lowest_f -6.92935e+11
(pid=19197) basinhopping step 0: f -5.34149e+11
(pid=19197) basinhopping step 1: f -5.34149e+11 trial_f 3.57728e+09 accepted 0  lowest_f -5.34149e+11
(pid=19184) basinhopping step 0: f -1.71201e+11
(pid=18662) basinhopping step 8: f -9.20021e+13 trial_f 1.28642e+10 accepted 0  lowest

...

(pid=42236) basinhopping step 4: f -6.63921e+11 trial_f 9.4088e+07 accepted 0  lowest_f -6.63921e+11
(pid=42237) basinhopping step 0: f -2.8931e+11
(pid=41085) basinhopping step 8: f -9.28231e+11 trial_f 6.86176e+07 accepted 0  lowest_f -9.28231e+11
(pid=41083) basinhopping step 7: f -6.40868e+13 trial_f 9.79936e+09 accepted 0  lowest_f -6.40868e+13
(pid=42237) basinhopping step 1: f -2.8931e+11 trial_f 2.53238e+08 accepted 0  lowest_f -2.8931e+11
(pid=38131) basinhopping step 8: f -3.15065e+11 trial_f 3.94495e+07 accepted 0  lowest_f -3.15065e+11
(pid=41085) basinhopping step 9: f -9.28231e+11 trial_f 222825 accepted 0  lowest_f -9.28231e+11
(pid=42236) basinhopping step 5: f -6.63921e+11 trial_f 9.43631e+07 accepted 0  lowest_f -6.63921e+11
(pid=42236) basinhopping step 6: f -6.63921e+11 trial_f 9.40049e+07 accepted 0  lowest_f -6.63921e+11
(pid=39886) basinhopping step 7: f -3.32088e+11 trial_f -3.32088e+11 accepted 1  lowest_f -3.32088e+11
(pid=39886) found new global minimum on st

(pid=45463) basinhopping step 1: f -3.06185e+11 trial_f -3.06185e+11 accepted 1  lowest_f -3.06185e+11
(pid=45463) found new global minimum on step 1 with function value -3.06185e+11
(pid=44764) basinhopping step 4: f -2.58025e+11 trial_f 2.0893e+08 accepted 0  lowest_f -2.58025e+11
(pid=45012) basinhopping step 0: f -6.12289e+11
(pid=44624) basinhopping step 7: f 2.7797e+07 trial_f 2.7797e+07 accepted 1  lowest_f 2.7797e+07
(pid=44624) found new global minimum on step 7 with function value 2.7797e+07
(pid=45463) basinhopping step 2: f -3.06185e+11 trial_f -1.19406e+11 accepted 0  lowest_f -3.06185e+11
(pid=44764) basinhopping step 5: f -2.58025e+11 trial_f 1.98613e+08 accepted 0  lowest_f -2.58025e+11
(pid=44624) basinhopping step 8: f 2.7797e+07 trial_f 1.39057e+09 accepted 0  lowest_f 2.7797e+07
(pid=44709) basinhopping step 3: f 6.66682e+07 trial_f 4.60696e+08 accepted 0  lowest_f 6.66682e+07
(pid=45463) basinhopping step 3: f -3.06185e+11 trial_f 4.99851e+08 accepted 0  lowest_f -

(pid=48275) basinhopping step 2: f 1.13335e+08 trial_f 2.21784e+09 accepted 0  lowest_f 1.13335e+08
(pid=47736) basinhopping step 6: f 1.34775e+08 trial_f 7.06632e+08 accepted 0  lowest_f 1.34775e+08
(pid=44763) basinhopping step 8: f -8.64652e+13 trial_f -8.64652e+13 accepted 1  lowest_f -8.64652e+13
(pid=44763) found new global minimum on step 8 with function value -8.64652e+13
(pid=45012) basinhopping step 7: f -1.72248e+12 trial_f -1.72248e+12 accepted 1  lowest_f -1.72248e+12
(pid=45012) found new global minimum on step 7 with function value -1.72248e+12
(pid=45462) basinhopping step 2: f -4.63061e+11 trial_f -3.57188e+11 accepted 0  lowest_f -4.63061e+11
(pid=48275) basinhopping step 3: f -5.73578e+11 trial_f -5.73578e+11 accepted 1  lowest_f -5.73578e+11
(pid=48275) found new global minimum on step 3 with function value -5.73578e+11
(pid=44763) basinhopping step 9: f -8.64652e+13 trial_f -8.58512e+13 accepted 0  lowest_f -8.64652e+13
(pid=48275) basinhopping step 4: f -5.73578e+

(pid=49443) basinhopping step 9: f -3.08399e+11 trial_f -1.10528e+09 accepted 0  lowest_f -3.08399e+11
(pid=45462) basinhopping step 10: f -4.63061e+11 trial_f 1.60608e+08 accepted 0  lowest_f -4.63061e+11
(pid=51839) basinhopping step 0: f 2.01591e+08
(pid=48276) basinhopping step 7: f -6.99413e+12 trial_f 7.79904e+10 accepted 0  lowest_f -6.99413e+12
(pid=51169) basinhopping step 2: f -2.81148e+11 trial_f 1.74631e+08 accepted 0  lowest_f -2.81148e+11
(pid=51169) basinhopping step 3: f -2.81148e+11 trial_f 1.74802e+08 accepted 0  lowest_f -2.81148e+11
(pid=48276) warning: basinhopping: local minimization failure
(pid=48276) basinhopping step 8: f -6.99413e+12 trial_f 1.0418e+09 accepted 0  lowest_f -6.99413e+12
(pid=51839) basinhopping step 1: f 2.01591e+08 trial_f 2.53598e+08 accepted 0  lowest_f 2.01591e+08
(pid=50217) basinhopping step 6: f -1.97242e+11 trial_f -1.97242e+11 accepted 1  lowest_f -1.97242e+11
(pid=50217) found new global minimum on step 6 with function value -1.97242

(pid=53501) basinhopping step 5: f -3.0308e+11 trial_f 1.25536e+08 accepted 0  lowest_f -3.0308e+11
(pid=53499) basinhopping step 3: f -1.59974e+11 trial_f 1.80932e+08 accepted 0  lowest_f -1.59974e+11
(pid=51839) basinhopping step 7: f -3.71875e+11 trial_f 2.56942e+08 accepted 0  lowest_f -3.71875e+11
(pid=50276) basinhopping step 8: f -5.77672e+11 trial_f -5.77672e+11 accepted 1  lowest_f -5.77672e+11
(pid=50276) found new global minimum on step 8 with function value -5.77672e+11
(pid=51839) basinhopping step 8: f -3.71875e+11 trial_f 2.01777e+08 accepted 0  lowest_f -3.71875e+11
(pid=50276) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=50276)   warnings.warn(warning_msg, ODEintWarning)
(pid=51840) basinhopping step 9: f -9.09195e+13 trial_f -9.09195e+13 accepted 1  lowest_f -9.09195e+13
(pid=51840) found new global

In [ ]:
for i in range(0,len(states)):    

    state=states[i]
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")

    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "WCASES"] = optimal[i][3]
    dfparam.at[j, "WREC"] = optimal[i][4]

    dfparam.to_csv("data/param_optimized_Yabox.csv", sep=",", index=False)
    dfparam
    